In [ ]:
#Lets have matplotlib "inline"
%matplotlib inline

# Add line profiler
%load_ext line_profiler

#Import packages we need
import numpy as np
from matplotlib import animation, rc
from matplotlib import pyplot as plt
from matplotlib.colorbar import ColorbarBase

from IPython.display import display, HTML

from enum import Enum
import time
import os
import json

try:
    from StringIO import StringIO
except ImportError:
    from io import StringIO

from GPUSimulators.common import Timer, DataDumper, ProgressPrinter
from GPUSimulators.model import EE2DKP07Dimsplit
from GPUSimulators.helpers import initial_conditions, visualization

In [ ]:
%setup_logging --out test_schemes.log logger

In [ ]:
%cuda_context_handler --no_autotuning my_context 

In [ ]:
#Set large figure sizes as default
rc('figure', figsize=(16.0, 12.0))
rc('animation', html='html5')
rc('animation', bitrate=1800)

In [ ]:
def plot_vars(rho, rho_u, rho_v, E):
    plt.figure()
    plt.subplot(1, 4, 1)
    plt.imshow(rho, origin='lower')
    plt.colorbar(orientation='horizontal', pad=0.02, shrink=0.9)

    plt.subplot(1, 4, 2)
    plt.imshow(rho_u, origin='lower')
    plt.colorbar(orientation='horizontal', pad=0.02, shrink=0.9)

    plt.subplot(1, 4, 3)
    plt.imshow(rho_v, origin='lower')
    plt.colorbar(orientation='horizontal', pad=0.02, shrink=0.9)

    plt.subplot(1, 4, 4)
    plt.imshow(E, origin='lower')
    plt.colorbar(orientation='horizontal', pad=0.02, shrink=0.9)

In [ ]:
def run_simulation(outfile, t_end, sim_args):
    with Timer("construct") as t:
        sim = EE2DKP07Dimsplit(**sim_args)
    print("Constructed in " + str(t.secs) + " seconds")

    #Create a netcdf file and simulate
    with DataDumper(outfile, mode='w', clobber=False) as outdata:
        outdata.nc.createDimension('time', None)
        outdata.nc.createDimension('x', sim.nx)
        outdata.nc.createDimension('y', sim.ny)

        #Create variables
        outdata.time_var = outdata.nc.createVariable('time', np.dtype('float32').char, 'time')
        outdata.x_var = outdata.nc.createVariable('x', np.dtype('float32').char, 'x')
        outdata.y_var = outdata.nc.createVariable('y', np.dtype('float32').char, 'y')
        outdata.rho_var = outdata.nc.createVariable('rho', np.dtype('float32').char, ('time', 'y', 'x'), zlib=True,
                                                    least_significant_digit=3)
        outdata.rho_u_var = outdata.nc.createVariable('rho_u', np.dtype('float32').char, ('time', 'y', 'x'),
                                                      zlib=True, least_significant_digit=3)
        outdata.rho_v_var = outdata.nc.createVariable('rho_v', np.dtype('float32').char, ('time', 'y', 'x'),
                                                      zlib=True, least_significant_digit=3)
        outdata.E_var = outdata.nc.createVariable('E', np.dtype('float32').char, ('time', 'y', 'x'), zlib=True,
                                                  least_significant_digit=3)

        #Create attributes
        def to_json(in_dict):
            out_dict = in_dict.copy()

            for key in out_dict:
                if isinstance(out_dict[key], np.ndarray):
                    out_dict[key] = out_dict[key].tolist()
                else:
                    try:
                        json.dumps(out_dict[key])
                    except:
                        out_dict[key] = str(out_dict[key])

            return json.dumps(out_dict)

        outdata.nc.created = time.ctime(time.time())
        outdata.nc.sim_args = to_json(sim_args)

        outdata.x_var[:] = np.linspace(0, sim.nx * sim.dx, sim.nx)
        outdata.y_var[:] = np.linspace(0, sim.ny * sim.dy, sim.ny)

        progress_printer = ProgressPrinter(n_save, print_every=10)
        print(f"Simulating to t={t_end}. Estimated {int(t_end / sim.dt)} timesteps (dt={sim.dt})")
        for i in range(n_save + 1):
            #Sanity check simulator
            try:
                sim.check()
            except AssertionError as e:
                print(f"Error after {sim.sim_steps()} steps (t={sim.sim_time()}: {str(e)}")
                return outdata.filename

            #Simulate
            if i > 0:
                sim.simulate(t_end / n_save)

            #Save to file
            #rho = sim.u0[0].download(sim.stream)
            rho, rho_u, rho_v, E = sim.download()
            outdata.time_var[i] = sim.sim_time()
            outdata.rho_var[i, :] = rho
            outdata.rho_u_var[i, :] = rho_u
            outdata.rho_v_var[i, :] = rho_v
            outdata.E_var[i, :] = E

            #Write progress to screen
            print_string = progress_printer.getPrintString(i)
            if print_string:
                print(print_string)

    return outdata.filename

In [ ]:
class VisType(Enum):
    Schlieren = 0
    Density = 1


def create_animation(infile, vis_type, vmin, vmax, save_anim=False, cmap=plt.cm.coolwarm, fig_args=None):
    fig = plt.figure(**fig_args)

    with DataDumper(infile, 'r') as indata:
        time = indata.nc.variables['time'][:]
        x = indata.nc.variables['x'][:]
        y = indata.nc.variables['y'][:]
        rho = indata.nc.variables['rho'][0]
        rho_u = indata.nc.variables['rho_u'][0]
        rho_v = indata.nc.variables['rho_v'][0]

        created = indata.nc.created
        sim_args = json.loads(indata.nc.sim_args)
        for key in sim_args:
            if isinstance(sim_args[key], list):
                sim_args[key] = "[...]"
        num_frames = len(time)
        print(f"{infile} created {created} contains {num_frames} timesteps")
        print("Simulator arguments: \n", sim_args)

        ax1 = fig.gca()
        extents = [0, x.max(), 0, y.max()]

        if vis_type == VisType.Schlieren:
            im = ax1.imshow(Visualization.gen_colors(rho, rho_u, rho_v, cmap, vmax, vmin), origin='lower',
                            extent=extents, cmap='gray', vmin=0.0, vmax=1.0)
            fig.suptitle("Schlieren / vorticity at t={:.2f}".format(time[0]))
        elif vis_type == VisType.Density:
            im = ax1.imshow(rho, origin='lower', extent=extents, cmap=cmap, vmin=vmin, vmax=vmax)
            fig.suptitle("Density at t={:.2f}".format(time[0]))
        else:
            assert False, "Wrong vis_type"

        #Create colorbar
        from matplotlib.colors import Normalize
        from mpl_toolkits.axes_grid1 import make_axes_locatable
        divider = make_axes_locatable(ax1)
        ax2 = divider.append_axes("right", size=0.1, pad=0.05)
        cb1 = ColorbarBase(ax2, cmap=cmap,
                           norm=Normalize(vmin=vmin, vmax=vmax),
                           orientation='vertical')

        #Label colorbar
        if vis_type == VisType.Schlieren:
            cb1.set_label('Vorticity')
        elif vis_type == VisType.Density:
            cb1.set_label('Density')

        progress_printer = ProgressPrinter(num_frames, print_every=5)

        def animate(i):
            rho = indata.nc.variables['rho'][i]
            rho_u = indata.nc.variables['rho_u'][i]
            rho_v = indata.nc.variables['rho_v'][i]

            if vis_type == VisType.Schlieren:
                im.set_data(Visualization.gen_colors(rho, rho_u, rho_v, cmap, vmax, vmin))
                fig.suptitle("Schlieren / vorticity at t={:.2f}".format(time[i]))
            elif vis_type == VisType.Density:
                im.set_data(rho)
                fig.suptitle("Density at t={:.2f}".format(time[i]))

            #Write progress to screen
            print_string = progress_printer.getPrintString(i)
            if print_string:
                print(print_string)

        anim = animation.FuncAnimation(fig, animate, interval=50, frames=range(num_frames))
        plt.close()

        if (save_anim):
            root, _ = os.path.splitext(infile)
            movie_outpath = os.path.abspath(root + ".mp4")
            if (os.path.isfile(movie_outpath)):
                print("Reusing previously created movie " + movie_outpath)
            else:
                print("Creating movie " + movie_outpath)
                #from matplotlib.animation import FFMpegFileWriter
                #writer = FFMpegFileWriter(fps=25)
                from matplotlib.animation import FFMpegWriter
                writer = FFMpegWriter(fps=25)
                anim.save(movie_outpath, writer=writer)
            display(HTML("""
            <div align="middle">
            <video width="80%" controls>
                <source src="{:s}" type="video/mp4">
            </video>
            </div>
            """.format(movie_outpath)))
        else:
            #plt.rcParams["animation.html"] = "html5"
            plt.rcParams["animation.html"] = "jshtml"
            display(anim)

# Shock-bubble

In [ ]:
nx = 400
arguments = InitialConditions.gen_shock_bubble(nx, nx // 4, 1.4)
plt.figure()
plt.imshow(Visualization.gen_schlieren(arguments['rho']), cmap='gray')
plt.colorbar(orientation='vertical', aspect=20, pad=0.02, shrink=0.3)

In [ ]:
nx = 800  #1600
ny = nx // 4
g = 0.0
gamma = 1.4
t_end = 0.5  #3.0
n_save = 20  #500
outfile = "data/euler_shock-bubble.nc"
outdata = None

arguments = InitialConditions.gen_shock_bubble(nx, ny, gamma)
arguments['context'] = my_context
outfile = run_simulation(outfile, t_end, arguments)

In [ ]:
#outfile = 'data/euler_shock-bubble_0008.nc'
create_animation(outfile, vis_type=VisType.Schlieren, vmin=-0.2, vmax=0.2, cmap=plt.cm.RdBu, save_anim=False,
                 fig_args={'figsize': (16, 5)})

# Kelvin-Helmholtz

In [ ]:
nx = 400
arguments = InitialConditions.gen_kelvin_helmholtz(nx, nx // 4, 1.4)

plt.figure()
plt.imshow(arguments['rho'])
plt.colorbar(orientation='vertical', aspect=20, pad=0.02, shrink=0.3)

In [ ]:
nx = 400
ny = nx // 2
roughness = 0.125
t_end = 10.0
n_save = 100  #1000
outfile = "data/euler_kelvin_helmholtz.nc"
outdata = None

arguments = InitialConditions.gen_kelvin_helmholtz(nx, ny, gamma, roughness)
arguments['context'] = my_context
outfile = run_simulation(outfile, t_end, arguments)

In [ ]:
#outfile='data/euler_kelvin_helmholtz_0012.nc'
create_animation(outfile, vis_type=VisType.Density, vmin=1.0, vmax=2.0, save_anim=False, fig_args={'figsize': (16, 9)})

# Rayleigh-Taylor

* Liska and Wendroff, COMPARISON OF SEVERAL DIFFERENCE SCHEMES ON 1D AND 2D TEST PROBLEMS FOR THE EULER EQUATIONS, http://www-troja.fjfi.cvut.cz/~liska/CompareEuler/compare8.pdf
* https://www.astro.princeton.edu/~jstone/Athena/tests/rt/rt.html
* 

In [ ]:
nx = 400
arguments = InitialConditions.gen_rayleigh_taylor(nx, nx * 3, 1.4, version=0)
plot_vars(arguments['rho'], arguments['rho_u'], arguments['rho_v'], arguments['E'])

In [ ]:
nx = 151
ny = nx * 3
g = 0.1
gamma = 1.4
t_end = 30
n_save = 300
outfile = "data/euler_rayleigh-taylor.nc"
outdata = None

arguments = InitialConditions.gen_rayleigh_taylor(nx, ny, gamma)
arguments['context'] = my_context
outfile = run_simulation(outfile, t_end, arguments)

In [ ]:
#outfile = 'data/euler_rayleigh-taylor_0007.nc'
create_animation(outfile, vis_type=VisType.Density, vmin=1, vmax=2, cmap=plt.cm.coolwarm, save_anim=False,
                 fig_args={'figsize': (3.4, 8)})